In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from pathlib import Path

try:
    from google.colab import drive

    drive.mount("/content/drive")
    workding_dir = "/content/drive/MyDrive/logical-reasoning/"
except ModuleNotFoundError:
    workding_dir = str(Path.cwd().parent)

In [3]:
import os
import sys
from pathlib import Path

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
need_to_setup_env = False
need_to_setup_env

False

In [5]:
if need_to_setup_env:
    %pip install -r requirements.txt
    %cd /content/
    %rm -rf LLaMA-Factory
    !git clone https://github.com/hiyouga/LLaMA-Factory.git
    %cd LLaMA-Factory
    %ls
    %pip install -e .[torch,bitsandbytes]
    
    os.chdir(workding_dir)
    sys.path.append(workding_dir)
    print("workding dir:", workding_dir)

In [6]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [7]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m None True datasets/mgtv results/mgtv-results_bf16.csv


In [8]:
!nvidia-smi

Thu Jul 11 17:21:42 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 545.23.07              Driver Version: 546.12       CUDA Version: 12.3     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA GeForce RTX 4080 ...    On  | 00000000:01:00.0 Off |                  N/A |
| N/A   50C    P8               2W / 150W |      0MiB / 12282MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [9]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 29.7 ms, sys: 12.1 ms, total: 41.8 ms
Wall time: 1.24 s


In [10]:
from llm_toolkit.logical_reasoning_utils import *

loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py


In [11]:
df_alpaca = load_alpaca_data(data_path)
df_alpaca.head()

loading existing data from: llama-factory/data/alpaca_mgtv_p1.json


instruction input output
0  你是一个逻辑游戏的主持人。游戏规则如下：\n\n1. 参与者会得到一个谜题。\n2. 参与者...           不是
1  你是一个逻辑游戏的主持人。游戏规则如下：\n\n1. 参与者会得到一个谜题。\n2. 参与者...           不是
2  你是一个逻辑游戏的主持人。游戏规则如下：\n\n1. 参与者会得到一个谜题。\n2. 参与者...          不重要
3  你是一个逻辑游戏的主持人。游戏规则如下：\n\n1. 参与者会得到一个谜题。\n2. 参与者...           不是
4  你是一个逻辑游戏的主持人。游戏规则如下：\n\n1. 参与者会得到一个谜题。\n2. 参与者...            是

In [12]:
def evaluate_model_all_epochs(model_name, adapter_path_base, num_train_epochs, start_epoch=0, load_in_4bit=True, num_of_entries=-1):
    os.environ["MODEL_NAME"] = model_name
    os.environ["LOAD_IN_4BIT"] = "true" if load_in_4bit else "false"
    for i in range(start_epoch, num_train_epochs + 1):
        print(f"Epoch {i}")
        if i == 0:
            os.unsetenv("ADAPTER_NAME_OR_PATH")
        else:
            adapter_path = f"{adapter_path_base}/checkpoint-{562 * i}"
            os.environ["ADAPTER_NAME_OR_PATH"] = adapter_path

        !python llm_toolkit/eval_logical_reasoning.py {num_of_entries}

In [13]:
%%time

evaluate_model_all_epochs("internlm/internlm2_5-7b-chat-1m", "llama-factory/saves/internlm2_5_7b/lora/sft_bf16", 3, start_epoch=0, load_in_4bit=False, num_of_entries=-1)

Epoch 0
loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env
Adding /home/inflaton/code/projects/courses/logical-reasoning to sys.path
loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
internlm/internlm2_5-7b-chat-1m None False datasets/mgtv results/mgtv-results_bf16.csv
(1) GPU = NVIDIA GeForce RTX 4080 Laptop GPU. Max memory = 11.994 GB.
0.0 GB of memory reserved.
loading model: internlm/internlm2_5-7b-chat-1m
Loading checkpoint shards: 100%|██████████████████| 8/8 [10:28<00:00, 78.57s/it]
(2) GPU = NVIDIA GeForce RTX 4080 Laptop GPU. Max memory = 11.994 GB.
8.834 GB of memory reserved.
loading train/test data files
Map: 100%|█████████████████████████| 3000/3000 [00:00<00:00, 3264.59 examples/s]
DatasetDict({
    train: Dataset({
        features: ['text', 'label', 'answer', 'title', 'puzzle', 'truth', 'train_text', 'prompt'],
        num_rows: 25000
    })
    test: Dataset({
        features: ['text',

In [14]:
%%time

evaluate_model_all_epochs("internlm/internlm2_5-7b-chat-1m", "llama-factory/saves/internlm2_5_7b/lora/sft_bf16", 4, start_epoch=4, load_in_4bit=False, num_of_entries=-1)

Epoch 4
loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env
Adding /home/inflaton/code/projects/courses/logical-reasoning to sys.path
loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py
internlm/internlm2_5-7b-chat-1m llama-factory/saves/internlm2_5_7b/lora/sft_bf16/checkpoint-2248 False datasets/mgtv results/mgtv-results_bf16.csv
(1) GPU = NVIDIA GeForce RTX 4080 Laptop GPU. Max memory = 11.994 GB.
0.0 GB of memory reserved.
loading model: internlm/internlm2_5-7b-chat-1m
[INFO|tokenization_utils_base.py:2161] 2024-07-12 08:47:38,496 >> loading file ./tokenizer.model from cache at /home/inflaton/.cache/huggingface/hub/models--internlm--internlm2_5-7b-chat-1m/snapshots/8d1a709a04d71440ef3df6ebbe204672f411c8b6/./tokenizer.model
[INFO|tokenization_utils_base.py:2161] 2024-07-12 08:47:38,497 >> loading file added_tokens.json from cache at None
[INFO|tokenization_utils_base.py:2161] 2024-07-12 08:47:38,497 >> l